# Accessibility Analysis using OpenRouteService

In [1]:
import folium
from folium import Map, Marker, FeatureGroup, LayerControl

from openrouteservice import client, geocode, directions, places

import numpy as np
from matplotlib import pylab
import pandas as pd 

import fiona as fn
import geojson 
from shapely.geometry import shape, Polygon, mapping
from shapely import wkt

from pprint import pprint

In [ ]:
# heatmap

In [2]:
#api_key = '58d904a497c67e00015b45fc2a6b6872037d44119582ef40cdf264c4' # Provide your personal API key
api_key = '58d904a497c67e00015b45fca522cb32f97347829754df32f76a48bb'
clnt = client.Client(key=api_key)
map_madagascar = folium.Map(tiles='Stamen Toner', location=([-18.812718, 46.713867]), zoom_start=5)

# Shapefiles from https://data.humdata.org/dataset/madagascar-administrative-boundary-shapefiles-level-1-4 (05/07/2018)
district_original = []
district_simp = []
with fn.open('mdg_polbnda_adm2_Distritcts_BNGRC_OCHA.shp', 'r') as districts:
    for polygon in districts:
        district_original.append(polygon)
        # Create geometry and simplify geometry
        geom = shape(polygon['geometry'])
        simp_geom = geom.simplify(0.0002, preserve_topology=False)
        simp_coord = mapping(simp_geom)
        folium.GeoJson(simp_coord).add_to(map_madagascar)
        district_simp.append(simp_coord)
        
    
# Health facilities from https://data.humdata.org/dataset/madagascar-healthsites (05/07/2018)
facility = []
with fn.open('healthsites.shp', 'r') as facility_data:
    for poi in facility_data:
        facility.append(poi)
    
#map_madagascar

In [15]:
len(district_original)

119

In [ ]:
'''
icon = folium.map.Icon(color='#fff3e6',
                        icon_color='red',
                        icon='hospital-symbol', # fetches font-awesome.io symbols
                        prefix='fa')
'''

In [3]:
print('There are {} health facilities.'.format(len(facility))) #

There are 121 health facilities.


In [ ]:
# eventuell isochrone exporten und in qgis verarbeiten?!

In [3]:
import time
def style_function(color):
    return lambda feature: dict(color=color)

# 1 hour Isochrones for foot walking and car driving
iso_foot = []
iso_car = []
iso_car_error = []
for loc in facility:
    try:
        iso_params = {'locations': loc['geometry']['coordinates'],
                          'profile': 'foot-walking',
                          'range_type': 'time',
                          'segments': 3600, # 3600=1hour
                          'attributes': {'total_pop', 'area'}}
        iso_foot_request = clnt.isochrones(**iso_params)
        lon, lat = loc['geometry']['coordinates']
        popup = "Meta Data: {}".format(iso_foot_request['features'][0]['properties']) ##
        folium.map.Marker([lat, lon]).add_to(map_madagascar)
        iso_foot.append(iso_foot_request)
        if len(iso_foot) % 39 == 0:
            time.sleep(60)
    except Exception as err:
        print(err)
        print(loc['geometry']['coordinates'])
        iso_car_error.append(loc['geometry']['coordinates'])
        pass
#map_madagascar

500 ({'error': {'code': 3099, 'message': 'Unable to build an isochrone map.'}, 'info': {'engine': {'version': '4.5.0', 'build_date': '2018-06-12T17:09:11Z'}, 'timestamp': 1531320499540}})
(47.3285816, -14.8355601)
500 ({'error': {'code': 3099, 'message': 'Unable to build an isochrone map.'}, 'info': {'engine': {'version': '4.5.0', 'build_date': '2018-06-12T17:36:31Z'}, 'timestamp': 1531320560913}})
(45.8711619, -16.008446)


In [4]:
print('There are {} health facilities.'.format(len(iso_foot)))

There are 119 health facilities.


In [5]:
map_madagascar

In [6]:
# isochrones for car
iso_car = []
iso_car_error = []
for loc in facility:
    try:
        iso_params = {'locations': loc['geometry']['coordinates'],
                          'profile': 'driving-car',
                          'range_type': 'time',
                          'segments': 3600, # 3600=1hour, 900=15min
                          'attributes': {'total_pop', 'area'}}
        iso_car_request = clnt.isochrones(**iso_params)
        iso_car.append(iso_car_request)
        if len(iso_car) % 39 == 0:
            time.sleep(60)
    except Exception as err:
        print(err)
        print(loc['geometry']['coordinates'])
        iso_car_error.append(loc['geometry']['coordinates'])
        pass

('Connection aborted.', OSError("(104, 'ECONNRESET')",))
(47.5310067, -18.9082844)
500 ({'error': {'code': 3099, 'message': 'Unable to build an isochrone map.'}, 'info': {'engine': {'version': '4.5.0', 'build_date': '2018-06-13T06:21:46Z'}, 'timestamp': 1531320901920}})
(47.3285816, -14.8355601)
500 ({'error': {'code': 3099, 'message': 'Unable to build an isochrone map.'}, 'info': {'engine': {'version': '4.5.0', 'build_date': '2018-06-12T14:47:57Z'}, 'timestamp': 1531320902473}})
(49.8509648, -17.001741)


In [25]:
# population per district
# http://www.worldpop.org.uk/data/files/index.php?dataset=571&zip_title=Madagascar%20100m%20Population&action=group (05.07.2018)
# Data were modified: intersected with district borders in qgis
district_pop = []
district_plot_data = []
pop_count = []
with fn.open('district_pop_final.shp', 'r') as dist_pop_data:
    for polygon in dist_pop_data:
        district_pop.append(polygon)
        district_name = polygon['properties']['REGION_NAM']
        district_code = polygon['properties']['DIST_PCODE']
        district_pop_count = round(polygon['properties']['sum'])
        pop_count.append(polygon['properties']['sum'])
        district_plot_data += [[district_name, district_code, district_pop_count]]

df_district = pd.DataFrame(data=district_plot_data, columns = ['District Name', 'District Code', 'Population Count'])
display(df_district)

total_pop = sum(pop_count)
print(sum(pop_count)) 

District Name District Code  Population Count
0          Analamanga   MDG11101001            323165
1          Analamanga   MDG11101002            248922
2          Analamanga   MDG11101003            173950
3          Analamanga   MDG11101004            331633
4          Analamanga   MDG11101005            406466
5          Analamanga   MDG11101006            169175
6          Analamanga      MDG11102            461396
7          Analamanga      MDG11103            507845
8          Analamanga      MDG11104            192866
9          Analamanga      MDG11106            259821
10         Analamanga      MDG11107            225434
11         Analamanga      MDG11115            216513
12         Analamanga      MDG11117            744751
13     Vakinankaratra      MDG12108            303506
14     Vakinankaratra      MDG12109            324196
15     Vakinankaratra      MDG12110            326014
16     Vakinankaratra      MDG12114            391913
17     Vakinankaratra      MDG12116            246010
18     Vakinankaratra      MDG12118            517156
19     Vakinankaratra      MDG12120            186234
20              Itasy      MDG13105            388079
21              Itasy      MDG13112            306316
22              Itasy      MDG13113            238267
23          Bongolava      MDG14111            416071
24          Bongolava      MDG14119            166012
25    Haute Matsiatra      MDG21201            242214
26    Haute Matsiatra      MDG21205            266520
27    Haute Matsiatra      MDG21208            273248
28    Haute Matsiatra      MDG21219            113745
29    Haute Matsiatra      MDG21220            215805
..                ...           ...               ...
89   Atsimo Andrefana      MDG51501            199441
90   Atsimo Andrefana      MDG51503             58172
91   Atsimo Andrefana      MDG51504            149126
92   Atsimo Andrefana      MDG51505             83437
93   Atsimo Andrefana      MDG51506            261321
94   Atsimo Andrefana      MDG51507            394750
95   Atsimo Andrefana      MDG51512            143915
96   Atsimo Andrefana      MDG51520            336370
97   Atsimo Andrefana      MDG51521             49274
98             Androy      MDG52513            139182
99             Androy      MDG52514            140181
100            Androy      MDG52516            445014
101            Androy      MDG52518            209675
102             Anosy      MDG53515            346014
103             Anosy      MDG53517            242873
104             Anosy      MDG53519            266105
105            Menabe      MDG54502             95674
106            Menabe      MDG54508            153324
107            Menabe      MDG54509            180132
108            Menabe      MDG54510            157985
109            Menabe      MDG54511            166453
110             Diana      MDG71713            134161
111             Diana      MDG71715            146377
112             Diana      MDG71717            275083
113             Diana      MDG71718             92918
114             Diana      MDG71719            242362
115              Sava      MDG72710            294598
116              Sava      MDG72711            387360
117              Sava      MDG72712            241658
118              Sava      MDG72716            324635

[119 rows x 3 columns]

27798005.428149853


In [49]:
# union der isochrone -> ist egal zu welchem Krankenhaus die gehen
map_madagascar = folium.Map(tiles='Stamen Toner', location=([-18.812718, 46.713867]), zoom_start=5)
iso_geom_foot = []
iso_union_foot = []
for iso in iso_foot:
    iso_geom = shape(iso['features'][0]['geometry'])
    if iso_geom.union(iso_geom):
        union_geom = iso_geom.union(iso_geom)
        union_coord = mapping(union_geom)
        swiched_coords = [(y,x) for x,y in union_coord['coordinates'][0]] # swap (x,y) to (y,x)
        folium.features.PolygonMarker(swiched_coords,
                            color='#ffd699',
                                     fill_color='#ffd699',
                                    fill_opacity=0.2,
                                     weight=3).add_to(map_madagascar)
        iso_union_foot.append(union_coord)
    iso_geom_foot.append(iso_geom)


In [50]:
map_madagascar

In [29]:
#### kann weg?
facility_polys = []
for iso in iso_foot:
    poly = iso['features'][0]['geometry']
    facility_polys.append(poly)
    
for polygon in districts:
    district_original.append(polygon)
    # Create geometry and simplify geometry
    geom = shape(polygon['geometry'])
    simp_geom = geom.simplify(0.0002, preserve_topology=False)
    simp_coord = mapping(simp_geom)
    folium.GeoJson(simp_coord).add_to(map_madagascar)
    district_simp.append(simp_coord)

In [28]:
# population in isochrones -> access to pois

plot_data_foot = []
for iso in iso_foot:
    coordinates = iso['features'][0]['properties']['center']
    #area = iso['features'][0]['properties']['area']
    pop_foot = iso['features'][0]['properties']['total_pop']
    total_area_km_foot = iso['features'][0]['properties']['total_area_km']
    access_foot = pop_foot/total_pop*100
    plot_data_foot += [[coordinates, pop_foot, total_area_km_foot, access_foot]]

plot_data_car = []
for iso in iso_car:
    pop_car = iso['features'][0]['properties']['total_pop']
    total_area_km_car = iso['features'][0]['properties']['total_area_km']
    access_car = pop_car/total_pop*100
    plot_data_car += [[pop_car, total_area_km_car, access_car]]
    
df_foot = pd.DataFrame(data=plot_data_foot, columns = ['Location', 'Foot: Population per Isochrone', 'Foot: Total Area [km]', 'Foot: Pop. with access [%]'])
display(df_foot)
df_car = pd.DataFrame(data=plot_data_car, columns = ['Car: Population per Isochrone', 'Car: Total Area [km]', 'Car: Pop. with access [%]'])
display(df_car)

Location  Foot: Population per Isochrone  \
0    [47.531007, -18.908284]                          579875   
1    [48.424307, -17.835671]                           23518   
2    [47.531205, -18.911203]                          562183   
3    [47.517277, -18.908799]                          528053   
4     [48.53984, -15.255391]                           13910   
5    [47.084759, -21.449607]                           11982   
6    [47.124065, -21.419086]                            4345   
7    [47.507367, -18.875619]                          591846   
8    [47.811356, -18.918928]                           15181   
9    [48.235671, -18.947332]                            7244   
10   [45.318194, -24.220357]                               0   
11   [47.241707, -20.541004]                           15759   
12    [46.906825, -18.95522]                           26465   
13    [47.085985, -21.44459]                           10753   
14   [47.562953, -18.894223]                          491476   
15   [46.990224, -21.628019]                            1653   
16    [48.927337, -15.04816]                            4909   
17   [47.500144, -20.216723]                            1515   
18   [47.324594, -20.454729]                             672   
19   [46.823213, -19.281393]                            2615   
20   [48.202353, -20.930524]                             860   
21   [47.348303, -18.923717]                            2634   
22   [47.788193, -22.490718]                            3371   
23   [49.202998, -12.497265]                               0   
24   [47.788346, -22.490695]                            3371   
25    [49.635448, -14.60753]                            3334   
26   [47.865916, -21.380825]                               0   
27   [47.043146, -19.875733]                           62898   
28   [48.582347, -15.376195]                             271   
29   [48.582513, -15.376166]                             271   
..                       ...                             ...   
89     [47.523301, -18.9211]                          378353   
90    [47.517937, -18.92082]                          368139   
91   [46.317831, -15.715342]                          151995   
92   [49.293637, -12.285183]                           46437   
93   [47.490671, -18.889972]                          295931   
94   [46.944415, -25.025978]                            8585   
95   [47.109938, -21.461869]                           11110   
96   [49.419984, -17.382086]                           22658   
97   [47.523157, -18.906724]                          593785   
98   [47.507331, -18.907812]                          419467   
99   [47.546302, -18.902532]                          539654   
100  [49.741686, -15.428855]                           53655   
101  [46.309726, -15.706598]                          137173   
102  [47.833134, -19.010847]                            2654   
103  [48.979581, -18.734795]                              68   
104  [48.425097, -17.836142]                           23518   
105   [47.522778, -18.91937]                          433278   
106  [47.182479, -24.779497]                             922   
107  [47.528907, -18.903302]                          720619   
108  [47.519264, -18.921991]                          365987   
109   [47.50715, -18.875784]                          591846   
110  [47.507252, -18.905037]                          440314   
111  [47.523745, -18.900659]                          702311   
112  [49.817955, -14.507142]                            9359   
113  [47.093285, -21.451516]                           11019   
114  [47.991128, -14.896427]                           23144   
115  [48.234788, -18.948164]                            7244   
116  [47.523823, -20.228863]                            1011   
117   [49.41212, -17.383231]                           22054   
118   [47.523737, -18.90425]                          655138   

     Foot: Total Area [km]  Foot: Pop. with access 

Car: Population per Isochrone  Car: Total Area [km]  \
0                           116654               84.1649   
1                          3438344             2034.4393   
2                          3438865             2036.0441   
3                            59417              105.6193   
4                           498719              746.8769   
5                           490457              716.9031   
6                          3283466             1927.7831   
7                          2084296             1088.3878   
8                            45103              214.5062   
9                            22721               90.9111   
10                          233536              299.8372   
11                          224154              324.0665   
12                          498673              804.2837   
13                         3283183             1995.2997   
14                          467003              782.3047   
15                            7003               62.2791   
16                           32860              107.5499   
17                           46532              224.0198   
18                           63651              240.6873   
19                            2056               61.3544   
20                         2783980             1031.6749   
21                          203674              204.3176   
22                           74531              121.3956   
23                          203674              204.3176   
24                          100822              207.7600   
25                           81851              159.1454   
26                          648313              635.6862   
27                           66644              106.8217   
28                           66644              106.8217   
29                           66644              106.8217   
..                             ...                   ...   
88                         3438992             2005.9095   
89                          153639              108.5463   
90                           76041              204.1307   
91                         3440127             1987.2489   
92                           29162              177.4358   
93                          505585              845.4497   
94                          203945              236.8566   
95                         3439269             2041.7608   
96                         3438914             2028.2440   
97                         3282552             2036.9883   
98                           87482              111.4524   
99                          153683              106.1029   
100                          65443              411.9935   
101                          35690              390.7904   
102                         116654               84.4717   
103                        3439466             2037.7882   
104                           2135               20.8251   
105                        3438341             2041.5763   
106                        3439401             2019.3028   
107                        3283466             1927.7831   
108                        3438731             2035.8041   
109                        3439242             2049.5508   
110                          44349               77.8787   
111                         498672              755.8853   
112                          79521              127.5645   
113                          47057              214.9386   
114                           8625               68.1842   
115                          18532               96.7755   
116                         230037              331.8364   
117                        3440221             2061.8943   

     Car: Pop. with access [%]  
0                     0.419649  
1                    12.369031  
2                    12.370906  
3                     0.213746  
4                     1.794082  
5                     1.764360  
6                    11.811876  
7                   

In [12]:
# % of population with access to health facilities per district

# isochrone überschneiden sich -> pop nicht doppelt zählen in der summe 
access_foot = []
for pop in plot_data_foot:
    access_foot.append(pop[1])
access_foot_sum = sum(access_foot)

access_car = []
for pop in plot_data_car:
    access_car.append(pop[0])
access_car_sum = sum(access_car)
print('In 2016/2017 Madagascar counted about 25 Million inhabitants. {:.0f} have access to health facilities on an 1 hour foot way, which are {:.2f}% of the total population and {:.0f} have access on an 1 hour car drive, which are {:.2f}%.'.format(access_foot_sum, access_foot_sum/total_pop*100, access_car_sum, access_car_sum/total_pop*100))

In 2016/2017 Madagascar counted about 25 Million inhabitants. 15852654 have access to health facilities on an 1 hour foot way, which are 63.41% of the total population and 126190583 have access on an 1 hour car drive, which are 504.76%.
